In [3]:
import pickle 
import numpy as np
import plotly.figure_factory as ff
import plotly.graph_objects as go

with open(r'datasets/df.pkl', 'rb') as f:
    db = pickle.load(f)

# Calculate statistics
mean_price = db['P [$/kWh]'].mean()
median_price = db['P [$/kWh]'].median()
std_price = db['P [$/kWh]'].std()

# Generate the distribution plot
fig_distribution = ff.create_distplot([db['P [$/kWh]'].values], ['P [$/kWh]'], bin_size=0.005)
fig_distribution.update_layout(title='Distribution of Hydro-Quebec Wholesale Electricity Rate', xaxis_title='Price [$/kWh]', yaxis_title='Density')

# Manually calculate the max y-value for the distribution plot
hist_data = np.histogram(db['P [$/kWh]'], bins=int((db['P [$/kWh]'].max() - db['P [$/kWh]'].min()) / 0.005))
max_y_value = max(hist_data[0]) / len(db['P [$/kWh]']) / 0.005

# Add lines for mean, median, and std deviation
fig_distribution.add_trace(go.Scatter(
    x=[mean_price, mean_price],
    y=[0, max_y_value],
    mode="lines",
    name="Mean",
    line=dict(color="Red", width=2)
))

fig_distribution.add_trace(go.Scatter(
    x=[median_price, median_price],
    y=[0, max_y_value],
    mode="lines",
    name="Median",
    line=dict(color="Green", width=2)
))

fig_distribution.add_trace(go.Scatter(
    x=[mean_price - std_price, mean_price - std_price],
    y=[0, max_y_value],
    mode="lines",
    name="Mean - Std Dev",
    line=dict(color="Blue", width=2, dash="dash")
))

fig_distribution.add_trace(go.Scatter(
    x=[mean_price + std_price, mean_price + std_price],
    y=[0, max_y_value],
    mode="lines",
    name="Mean + Std Dev",
    line=dict(color="Blue", width=2, dash="dash")
))

# Show the distribution plot
fig_distribution.show()

print(f"Mean Price: {mean_price:.6f} $/kWh")
print(f"Median Price: {median_price:.6f} $/kWh")
print(f"Standard Deviation: {std_price:.6f} $/kWh")
print(f"Minimum Price: {db['P [$/kWh]'].min():.6f} $/kWh")
print(f"Maximum Price: {db['P [$/kWh]'].max():.6f} $/kWh")

Mean Price: 0.051296 $/kWh
Median Price: 0.028252 $/kWh
Standard Deviation: 0.091760 $/kWh
Minimum Price: -0.250710 $/kWh
Maximum Price: 2.453611 $/kWh


In [14]:
with open(r'res/agg_res.pkl', 'rb') as f:
    res = pickle.load(f)
res['db']

cos       sin  Temp [°C]  pv [kWh]   
Time                                                           
2018-02-19 00:00:00  1.000000  0.500000  -5.196000       0.0  \
2018-02-19 00:05:00  0.999881  0.510907  -5.309333       0.0   
2018-02-19 00:10:00  0.999524  0.521810  -5.422667       0.0   
2018-02-19 00:15:00  0.998929  0.532702  -5.536000       0.0   
2018-02-19 00:20:00  0.998097  0.543578  -5.544000       0.0   
...                       ...       ...        ...       ...   
2018-02-25 23:35:00  0.997028  0.445567   1.832333       0.0   
2018-02-25 23:40:00  0.998097  0.456422   1.786667       0.0   
2018-02-25 23:45:00  0.998929  0.467298   1.741000       0.0   
2018-02-25 23:50:00  0.999524  0.478190   1.684333       0.0   
2018-02-25 23:55:00  0.999881  0.489093   1.627667       0.0   

                     non_reducible [kWh]  reducible [kWh]  heating [kWh]   
Time                                                                       
2018-02-19 00:00:00             0.531444              0.0      19.776444  \
2018-02-19 00:05:00             0.531444              0.0      19.776444   
2018-02-19 00:10:00             0.531444              0.0      19.776444   
2018-02-19 00:15:00             2.931444              0.0       5.269778   
2018-02-19 00:20:00             2.931444              0.0       5.269778   
...                                  ...              ...            ...   
2018-02-25 23:35:00             3.840000              0.0      18.417778   
2018-02-25 23:40:00             3.840000              0.0      18.417778   
2018-02-25 23:45:00             2.263222              0.0      21.880444   
2018-02-25 23:50:00             2.263222              0.0      21.880444   
2018-02-25 23:55:00             2.263222              0.0      21.880444   

                     P [$/kWh]  Des Temp [°C]  peak  working_day  
Time                                                              
2018-02-19 00:00:00   0.027211           18.0     0            1  
2018-02-19 00:05:00   0.029832           18.0     0            1  
2018-02-19 00:10:00   0.029778           18.0     0            1  
2018-02-19 00:15:00   0.029467           18.0     0            1  
2018-02-19 00:20:00   0.013970           18.0     0            1  
...                        ...            ...   ...          ...  
2018-02-25 23:35:00   0.001729           18.0     0            0  
2018-02-25 23:40:00   0.001729           18.0     0            0  
2018-02-25 23:45:00   0.001729           18.0     0            0  
2018-02-25 23:50:00   0.003851           18.0     0            0  
2018-02-25 23:55:00   0.002783           18.0     0            0  

[2016 rows x 11 columns]

In [45]:
def hvac_alg_comparision():
    with open(r'res/agg_res.pkl', 'rb') as f:
        res = pickle.load(f)
    # temperatures

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=res['db'].index, y=res['db']['Des Temp [°C]'], name='desired inside temperature'))
    fig.add_trace(go.Scatter(x=res['db'].index, y=res['agg_main_Tin'], name='new inside temperature'))
    fig.add_trace(go.Scatter(x=res['db'].index, y=res['db']['Temp [°C]'], name='outdoor temperature'))
    fig.update_layout(title='Change in average inside temperature',xaxis_title='Time',yaxis_title='C')
    fig.show()

    print(f'total cost: {res["agg_total_cost"]}')

    main_load_peak_hours = res['agg_load_total'] * res['db']['peak']
    ref_load_peak_hours = res['agg_ref_total_load'] * res['db']['peak']
    diff_load_peak_hours = ref_load_peak_hours - main_load_peak_hours
    print(f'total saved consumption during peak hours: {diff_load_peak_hours.sum()}')
    print(f'peak load shaved: {ref_load_peak_hours.max()-main_load_peak_hours.max()}')

In [43]:
# Status Quo
hvac_alg_comparision()

total hvac cost: 24572.661202927018
total saved consumption during peak hours: 10282.308315313538
peak load shaved: 0.0


In [46]:
# turn hvac off
hvac_alg_comparision()

total cost: -152641.21522423255
total saved consumption during peak hours: 292442.30831531354
peak load shaved: 1641.893391291775


In [47]:
# hueristic -0.5
hvac_alg_comparision()

total cost: 25730.368668007017
total saved consumption during peak hours: 8762.308315313543
peak load shaved: 6.06577777777602


In [48]:
# hueristic -2
hvac_alg_comparision()

total cost: 13821.741406407022
total saved consumption during peak hours: 27882.308315313545
peak load shaved: 94.40809835476239


In [49]:
# d3qn
hvac_alg_comparision()

total cost: 3120.35410154702
total saved consumption during peak hours: 49462.30831531355
peak load shaved: 523.8648888888881


In [50]:
# ppod
hvac_alg_comparision()

total cost: 3339.5609318270194
total saved consumption during peak hours: 49302.30831531355
peak load shaved: 608.3164444444442


In [51]:
# sacd
hvac_alg_comparision()

total cost: -2145.6605710329777
total saved consumption during peak hours: 59102.30831531355
peak load shaved: 243.84000000000015


In [52]:
# sacd
hvac_alg_comparision()

total cost: 4022.769849147023
total saved consumption during peak hours: 48022.30831531355
peak load shaved: 278.31822222222354


In [54]:
fig = go.Figure()

# Add reference controllable load as an area chart
fig.add_trace(go.Scatter(
    x=res['db'].index, 
    y=res['agg_ref_ctrl_load'], 
    name='Reference Controllable Load',
    fill='tozeroy',  # Fills the area below the line
    mode='none'  # No markers or lines, just the filled area
))

# Add new controllable load as a line chart
fig.add_trace(go.Scatter(
    x=res['db'].index, 
    y=res['agg_load_ctrl'], 
    name='New Controllable Load',
    mode='lines'
))

fig.show()

In [55]:
import plotly.graph_objs as go
import pandas as pd

trace_nonreducible = go.Scatter(
    x=res['db'].index,
    y=res['agg_total_nonreducible'],
    mode='lines',
    name='Non-Reducible',
    stackgroup='one'
)

trace_ctrl = go.Scatter(
    x=res['db'].index,
    y=res['agg_load_ctrl'],
    mode='lines',
    name='Controllable',
    stackgroup='one'
)

trace_hvac = go.Scatter(
    x=res['db'].index,
    y=res['agg_load_hvac'],
    mode='lines',
    name='HVAC',
    stackgroup='one'
)

# Combine traces into a figure
fig = go.Figure(data=[trace_nonreducible, trace_ctrl, trace_hvac])

# Update layout
fig.update_layout(
    title='Stacked Area Plot of New Load Components',
    xaxis_title='Time',
    yaxis_title='Load',
    template='plotly_white'
)

# Show plot
fig.show()

fig = px.line(x=res['db'].index, y=[res['agg_ref_ctrl_load'], res['agg_load_ctrl']])
fig.show()

In [19]:
px.line(x= res['db'].index, y=[res['agg_cost_components'][:,1], res['agg_cost_components'][:,2]])

In [56]:
res['agg_cost_components'].sum(axis=0)

array([ 7190.48546847, 25669.63419193, 17696.5735583 ])

sens on temp
sens on alpha
sens on beta
sens on gamma
carbon footprint